In [0]:
# from pyspark.sql import SparkSession
# from pyspark.sql.functions import *
# from pyspark.sql.types import *
from pyspark.sql.window import Window

df = spark.read.csv(
    "/Volumes/workspace/default/port/Fraudulent_E-Commerce_Transaction_Data.csv",
    header=True,
    inferSchema=True
)
display(df)

df = df.withColumn("transaction_date", to_timestamp("transaction_date", "dd/MM/yyyy HH:mm"))
df = df.withColumn("transaction_amount", col("transaction_amount").cast("double"))
 
df = df.withColumn(
    "transaction_amount_clean", 
    regexp_extract(
        col("transaction_amount"), 
        r'(\d+\.?\d*)', 
        1
    ).cast("double")
).withColumn(
    "transaction_amount_clean",
    when(
        col("transaction_amount_clean").isNull() | (col("transaction_amount_clean") == 0), 
        None
    ).otherwise(col("transaction_amount_clean"))
)

df = df.withColumn(
    "payment_method_clean",
    when(lower(col("payment_method")).rlike("credit|card"), "credit card")
    .when(lower(col("payment_method")).rlike("debit"), "debit card")
    .when(lower(col("payment_method")).rlike("paypal"), "paypal")
    .when(lower(col("payment_method")).rlike("bank|transfer"), "bank transfer")
    .when(lower(col("payment_method")).rlike("cash"), "cash")
    .otherwise("Unknown")
)

display(
    df.groupBy(
        "Customer ID",
        "transaction_amount",
        "transaction_date"
    ).count().filter(col("count") > 1)
)

customer_stats = df.groupBy("Customer ID").agg(
    count("Transaction ID").alias("total_transactions"),
    avg("transaction_amount").alias("avg_transaction_amount"),
    stddev("transaction_amount").alias("transaction_amount_std"),
    min("transaction_date").alias("first_transaction"),
    max("transaction_date").alias("last_transaction")
)

window_spec = Window.partitionBy("Customer ID").orderBy("Transaction_Amount")
df = df.withColumn("amount_percentile", percent_rank().over(window_spec))

Transaction ID Customer ID Transaction Amount Transaction Date Payment Method Product Category Quantity Customer Age Customer Location Device Used IP Address Shipping Address Billing Address Is Fraudulent Account Age Days Transaction Hour c12e07a0-8a06-4c0d-b5cc-04f3af688570 8ca9f102-02a4-4207-ab63-484e83a1bdf0 42.32 24/03/2024 23:42 PayPal electronics 1 40 East Jameshaven desktop 110.87.246.85 5399 Rachel Stravenue Suite 718
 null null null null North Blakeburgh IL 78600" 5399 Rachel Stravenue Suite 718
 null null null null null null null null null null null null null North Blakeburgh IL 78600" 0 282 23 null null null null null null null null null null null 7d187603-7961-4fce-9827-9698e2b6a201 4d158416-caae-4b09-bd5b-15235deb9129 301.34 22/01/2024 00:53 credit card electronics 3 35 Kingstad tablet 14.73.104.153 5230 Stephanie Forge
 null null null null Collinsbury PR 81853" 5230 Stephanie Forge
 null null null null null null null null null null null null null Collinsbury PR 81853" 0 223 0 null null null null null null null null null null null f2c14f9d-92df-4aaf-8931-ceaf4e63ed72 ccae47b8-75c7-4f5a-aa9e-957deced2137 340.32 22/01/2024 08:06 debit card toys & games 5 29 North Ryan desktop 67.58.94.93 195 Cole Oval
 null null null null Port Larry IA 58422" 4772 David Stravenue Apt. 447
 null null null null null null null null null null null null null Velasquezside KS 67650" 0 360 8 null null null null null null null null null null null e9949bfa-194d-486b-84da-9565fca9e5ce b04960c0-aeee-4907-b1cd-4819016adcef 95.77 16/01/2024 20:34 credit card electronics 5 45 Kaylaville mobile 202.122.126.216 7609 Cynthia Square
 null null null null West Brenda NV 23016" 7609 Cynthia Square
 null null null null null null null null null null null null null West Brenda NV 23016" 0 325 20 null null null null null null null null null null null 7362837c-7538-434e-8731-0df713f5f26d de9d6351-b3a7-4bc7-9a55-8f013eb66928 77.45 16/01/2024 15:47 credit card clothing 5 42 North Edwardborough desktop 96.77.232.76 2494 Robert Ramp Suite 313
 null null null null Robinsonport AS 52039" 2494 Robert Ramp Suite 313
 null null null null null null null null null null null null null Robinsonport AS 52039" 0 116 15 null null null null null null null null null null null 5da506fe-d4df-474a-b773-146333f06cfe 03033baf-2bcc-4608-b5b8-9c86976f4948 345.27 22/02/2024 13:49 PayPal toys & games 1 9 Johnsonmouth desktop 158.48.161.135 PSC 3832, Box 5265
 null null null null APO AE 85694" PSC 3832, Box 5265
 null null null null null null null null null null null null null null APO AE 85694" 0 251 13 null null null null null null null null null null null null 47b35c5d-d4c9-4a7d-a354-cd41596abf67 6a5305a3-b47c-4bdb-91d7-3bf126530e01 53.69 21/03/2024 13:42 debit card toys & games 3 41 New Brendamouth mobile 93.54.173.138 272 Tammy Isle Apt. 969
 null null null null North Michaelmouth MH 02615" 272 Tammy Isle Apt. 969
 null null null null null null null null null null null null null North Michaelmouth MH 02615" 0 138 13 null null null null null null null null null null null bf3db41c-25a9-4e6d-b87f-13e5fabe35dd 7300dcf3-df6f-439f-ba13-a98f18b972f3 680.17 18/01/2024 23:25 debit card electronics 5 39 South Tracy tablet 61.52.160.51 30470 Amanda Causeway Suite 446
 null null null null Lake Ashleyland FM 97864" 30470 Amanda Causeway Suite 446
 null null null null null null null null null null null null null Lake Ashleyland FM 97864" 0 36 23 null null null null null null null null null null null 8ec806af-c367-4dd0-8218-25d3c8c7a346 25c48d47-879f-49b3-b0cc-a7393c28f8af 126.5 12/02/2024 04:01 debit card home & garden 4 35 West Henry mobile 6.59.118.143 179 Amy Roads
 null null null null Ryanland OH 38054" 179 Amy Roads
 null null null null null null null null null null null null null Ryanland OH 38054" 0 188 4 null null null null null null null null null null null 3b51c8cd-e0d7-48ba-894f-8f77b2cf2f43 41803857-0031-499c-bcaf-bca4e4ef4620 47.18 06/04/2024 22:52 bank transfer toys & games 4 19 T

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-8300697005452028>, line 42
     16 df = df.withColumn(
     17     "transaction_amount_clean", 
     18     regexp_extract(
   (...)
     28     ).otherwise(col("transaction_amount_clean"))
     29 )
     31 df = df.withColumn(
     32     "payment_method_clean",
     33     when(lower(col("payment_method")).rlike("credit|card"), "credit card")
   (...)
     38     .otherwise("Unknown")
     39 )
     41 display(
---> 42     df.groupBy(
     43         "Customer ID",
     44         "transaction_amount",
     45         "transaction_date"
     46     ).count().filter(col("count") > 1)
     47 )
     49 customer_stats = df.groupBy("Customer ID").agg(
     50     count("Transaction ID").alias("total_transactions"),
     51     avg("transaction_amount").alias("avg_transaction_amount"),
   (...)
     54     max("transaction_da